# Data Preprocessing

In [3]:
import pandas as pd
import os
from glob import glob
from tqdm import tqdm
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
import pyupbit
import math

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader, Dataset

In [4]:
class preprocessing() :
    def __init__(self, ticker, interval, to, count) :
        self.o_dataset = pyupbit.get_ohlcv(ticker=ticker, interval=interval, to=to, count=count)
        self.data, self.label = self.preprocess(self.o_dataset)
        
    def drop_feature(self, dataset_df) :
        # index(시간) 제거 
        dataset_df = dataset_df.reset_index(drop=True)
        return dataset_df
    
    def add_after10(self, dataset_df) :
        after10 = np.zeros_like(dataset_df['close'])
        for i in range(len(dataset_df['close']) - 1) :
            if dataset_df['close'][i + 1] > dataset_df['close'][i] :
                after10[i] = 1
            else : 
                after10[i] = 0
            
        return after10
    
    def add_avgPrice(self, dataset_df) :
        return (dataset_df['high'] + dataset_df['low'] + 
                dataset_df['open'] + dataset_df['close']) // 4    
    
    def preprocess(self, df) :
        dataset_df = self.drop_feature(df)
        dataset_df['avg_price'] = self.add_avgPrice(dataset_df)
        dataset_df['after10'] = self.add_after10(dataset_df)
        
        data = dataset_df.iloc[:-1]
        
        return data.drop(columns=['after10']), data['after10']
        
    

In [26]:
ticker = 'KRW-BTC'
interval ='minute10'
to = f'2022-02-24 00:00'
count = 10000

processed_data =  preprocessing(ticker, interval, to, count)
display(processed_data.data)
display(processed_data.label)

open        high         low       close      volume  \
0     46002000.0  46057000.0  45767000.0  46025000.0   30.031757   
1     46025000.0  46090000.0  45881000.0  45900000.0   13.966785   
2     45900000.0  45984000.0  45865000.0  45898000.0    9.401209   
3     45899000.0  46740000.0  45899000.0  46299000.0  104.885381   
4     46246000.0  47460000.0  46239000.0  47433000.0  377.836287   
5     47434000.0  47434000.0  45690000.0  45950000.0  300.847083   
6     45950000.0  46845000.0  45950000.0  46530000.0  128.721509   
7     46530000.0  46848000.0  46032000.0  46784000.0  128.186073   
8     46784000.0  46819000.0  45900000.0  46004000.0  148.200837   
9     45966000.0  46367000.0  45897000.0  45980000.0   82.858644   
10    45968000.0  45969000.0  45385000.0  45385000.0  163.310610   
11    45370000.0  45625000.0  45000000.0  45051000.0  163.702297   
12    45020000.0  45669000.0  45000000.0  45516000.0  143.852707   
13    45516000.0  45599000.0  45000000.0  45327000.0   81.079255   
14    45337000.0  45505000.0  45187000.0  45272000.0   67.488405   
15    45311000.0  45447000.0  45208000.0  45347000.0   36.101039   
16    45391000.0  45473000.0  45277000.0  45395000.0   39.768931   
17    45395000.0  45400000.0  45270000.0  45272000.0   29.192635   
18    45270000.0  45272000.0  45006000.0  45177000.0   68.720920   
19    45177000.0  45211000.0  44802000.0  44811000.0  103.446252   
20    44829000.0  44980000.0  44712000.0  44728000.0   63.858530   
21    44728000.0  44811000.0  44636000.0  44676000.0   86.141487   
22    44667000.0  44816000.0  44521000.0  44592000.0  100.716812   
23    44580000.0  44659000.0  44525000.0  44581000.0   46.474489   
24    44609000.0  44658000.0  44536000.0  44615000.0   39.680829   
25    44611000.0  44969000.0  44610000.0  44946000.0   67.496686   
26    44946000.0  44947000.0  44631000.0  44762000.0   63.297666   
27    44763000.0  44842000.0  44659000.0  44842000.0   44.917008   
28    44842000.0  44972000.0  44804000.0  44958000.0   69.278177   
29    44965000.0  45248000.0  44956000.0  45092000.0   80.880841   
30    45091000.0  45300000.0  45045000.0  45277000.0   53.026929   
31    45277000.0  45322000.0  45232000.0  45240000.0   38.201035   
32    45240000.0  45267000.0  45165000.0  45218000.0   42.614332   
33    45218000.0  45222000.0  45021000.0  45100000.0   37.371249   
34    45100000.0  45404000.0  45012000.0  45403000.0   86.969135   
35    45403000.0  45494000.0  45337000.0  45462000.0   60.682039   
36    45450000.0  45650000.0  45380000.0  45567000.0   63.035180   
37    45558000.0  45567000.0  45349000.0  45501000.0   47.154969   
38    45511000.0  45623000.0  45500000.0  45548000.0   37.007258   
39    45548000.0  45554000.0  45440000.0  45478000.0   36.290036   
40    45470000.0  45470000.0  45177000.0  45207000.0   43.428159   
41    45203000.0  45250000.0  44951000.0  44964000.0   75.007704   
42    44965000.0  45038000.0  44830000.0  44984000.0   53.511783   
43    44984000.0  44984000.0  44360000.0  44405000.0  132.096129   
44    44415000.0  44558000.0  44350000.0  44370000.0   91.338248   
45    44377000.0  44430000.0  44025000.0  44069000.0  134.607325   
46    44068000.0  44188000.0  44009000.0  44147000.0   88.973096   
47    44147000.0  44259000.0  44115000.0  44244000.0   68.345541   
48    44252000.0  44252000.0  43960000.0  44121000.0  120.843211   
49    44121000.0  44197000.0  43978000.0  44096000.0   65.317733   
50    44096000.0  44353000.0  44047000.0  44284000.0   87.663791   
51    44283000.0  44389000.0  44241000.0  44348000.0   42.603470   
52    44348000.0  44614000.0  44343000.0  44613000.0   52.514106   
53    44613000.0  44614000.0  44429000.0  44546000.0   51.403818   
54    44549000.0  44590000.0  44500000.0  44546000.0   25.245052   
55    44546000.0  44547000.0  44346000.0  44346000.0   37.971585   
56    44378000.0  44378000.0  43788000.0  43789000.0  134.784816   
57    43789000.0  44067000.0  43786000.0  44011000.0   67.551812   


0       0.0
1       0.0
2       1.0
3       1.0
4       0.0
5       1.0
6       1.0
7       0.0
8       0.0
9       0.0
10      0.0
11      1.0
12      0.0
13      0.0
14      1.0
15      1.0
16      0.0
17      0.0
18      0.0
19      0.0
20      0.0
21      0.0
22      0.0
23      1.0
24      1.0
25      0.0
26      1.0
27      1.0
28      1.0
29      1.0
30      0.0
31      0.0
32      0.0
33      1.0
34      1.0
35      1.0
36      0.0
37      1.0
38      0.0
39      0.0
40      0.0
41      1.0
42      0.0
43      0.0
44      0.0
45      1.0
46      1.0
47      0.0
48      0.0
49      1.0
50      1.0
51      1.0
52      0.0
53      0.0
54      0.0
55      0.0
56      1.0
57      1.0
58      0.0
59      0.0
60      1.0
61      1.0
62      1.0
63      0.0
64      1.0
65      0.0
66      1.0
67      1.0
68      0.0
69      0.0
70      1.0
71      0.0
72      1.0
73      0.0
74      1.0
75      0.0
76      1.0
77      1.0
78      0.0
79      0.0
80      1.0
81      0.0
82      1.0
83  

In [27]:
processed_data.data.to_csv('./4000_data.csv')
processed_data.label.to_csv('./4000_label.csv')

In [7]:
# csv_data = processed_data.data
# csv_label = processed_data.label

In [40]:
csv_data = pd.read_csv('./10000_data.csv').drop(columns=['Unnamed: 0'])
csv_label = pd.read_csv('./10000_label.csv').drop(columns=['Unnamed: 0'])

In [41]:
csv_data

open        high         low       close      volume  \
0     60903000.0  61141000.0  60871000.0  60916000.0   63.779659   
1     60916000.0  61046000.0  60769000.0  60883000.0   49.432295   
2     60879000.0  61300000.0  60878000.0  61106000.0   63.045267   
3     61142000.0  61299000.0  61095000.0  61233000.0   42.521032   
4     61233000.0  61244000.0  61151000.0  61200000.0   32.518230   
5     61200000.0  61220000.0  61140000.0  61145000.0   35.388684   
6     61145000.0  61145000.0  61056000.0  61062000.0   43.336748   
7     61063000.0  61240000.0  61049000.0  61198000.0   67.962853   
8     61196000.0  61249000.0  60900000.0  60938000.0  105.844950   
9     60938000.0  61440000.0  60938000.0  61432000.0   97.289920   
10    61432000.0  61519000.0  61386000.0  61439000.0  110.870231   
11    61442000.0  61443000.0  61243000.0  61370000.0   79.521331   
12    61370000.0  61650000.0  61368000.0  61645000.0   78.199001   
13    61646000.0  61660000.0  61400000.0  61419000.0   54.312355   
14    61400000.0  61430000.0  61033000.0  61070000.0   51.186595   
15    61070000.0  61108000.0  60897000.0  60909000.0   63.135771   
16    60910000.0  61100000.0  60900000.0  60900000.0   44.588205   
17    60900000.0  60900000.0  60800000.0  60835000.0   70.377625   
18    60837000.0  60837000.0  60700000.0  60802000.0   57.186062   
19    60800000.0  60873000.0  60770000.0  60862000.0   41.376500   
20    60860000.0  60976000.0  60846000.0  60918000.0   34.980476   
21    60918000.0  61000000.0  60902000.0  60905000.0   31.955973   
22    60904000.0  60980000.0  60854000.0  60964000.0   23.980232   
23    60980000.0  60998000.0  60962000.0  60988000.0   26.646769   
24    60988000.0  61016000.0  60940000.0  60999000.0   24.096548   
25    61000000.0  61034000.0  60960000.0  60977000.0   30.854002   
26    60977000.0  61000000.0  60950000.0  60973000.0   18.145168   
27    60973000.0  60989000.0  60800000.0  60800000.0   30.736614   
28    60801000.0  60802000.0  60654000.0  60671000.0   41.955329   
29    60671000.0  60671000.0  60505000.0  60600000.0   46.318292   
30    60612000.0  60699000.0  60600000.0  60698000.0   22.867369   
31    60698000.0  60698000.0  60647000.0  60664000.0   26.636227   
32    60664000.0  60868000.0  60661000.0  60726000.0   34.746895   
33    60751000.0  60751000.0  60623000.0  60653000.0   34.581096   
34    60654000.0  60682000.0  60506000.0  60682000.0   40.882030   
35    60682000.0  60682000.0  60550000.0  60613000.0   28.351046   
36    60605000.0  60650000.0  60512000.0  60642000.0   28.937719   
37    60642000.0  60741000.0  60642000.0  60731000.0   49.142320   
38    60726000.0  60768000.0  60520000.0  60521000.0   42.533907   
39    60542000.0  60883000.0  60521000.0  60723000.0  116.427886   
40    60723000.0  60967000.0  60676000.0  60842000.0  145.436923   
41    60807000.0  60842000.0  60754000.0  60757000.0   79.449825   
42    60797000.0  60800000.0  60548000.0  60566000.0   80.798858   
43    60566000.0  60643000.0  60448000.0  60448000.0   98.329919   
44    60447000.0  60641000.0  60410000.0  60499000.0   76.362810   
45    60499000.0  60718000.0  60465000.0  60696000.0   94.400546   
46    60696000.0  60827000.0  60649000.0  60811000.0  120.907754   
47    60816000.0  60817000.0  60658000.0  60767000.0  101.418095   
48    60710000.0  60862000.0  60700000.0  60854000.0   70.487917   
49    60854000.0  60954000.0  60787000.0  60848000.0  118.308884   
50    60851000.0  60959000.0  60802000.0  60913000.0   84.905559   
51    60918000.0  60921000.0  60778000.0  60845000.0   41.374904   
52    60845000.0  60921000.0  60807000.0  60890000.0   36.373901   
53    60890000.0  60920000.0  60790000.0  60876000.0   48.528741   
54    60895000.0  60920000.0  60809000.0  60812000.0   52.586751   
55    60812000.0  60950000.0  60699000.0  60874000.0   67.504839   
56    60874000.0  60918000.0  60800000.0  60830000.0   71.614609   
57    60842000.0  60910000.0  60830000.0  60842000.0  100.282157   


https://doheon.github.io/%EC%BD%94%EB%93%9C%EA%B5%AC%ED%98%84/time-series/ci-4.transformer-post/

참고해서 WindowDataset 구성하기

In [42]:
def _EachColumnMinMax(df_data) :
    norm = MinMaxScaler()
    for col in df_data.columns :
        df_2d = np.array(df_data[col].values).reshape(-1, 1)
        df_data[col] = norm.fit_transform(df_2d).squeeze(1)
    print(type(df_data))
    return df_data

def EachColumnMinMax(df_data) :
    norm = MinMaxScaler()
    df_data = norm.fit_transform(np.array(df_data).reshape(-1, 1)).squeeze(1)
    return df_data

def WindowDataGenerator(df_data, df_label, window_size, stride) :
    num_sample = (df_data.shape[0] - window_size) // stride + 1     

    data = np.zeros([window_size, df_data.shape[1], num_sample])
    labels = np.zeros([num_sample])

    for i in range(num_sample) :
        data_start = stride * i
        data_end = data_start + window_size
        data[:, :, i] = df_data[data_start : data_end, :]
        labels[i] = df_label[data_end - 1]

    data = data.transpose((2, 0, 1))
    print("dataset shape ==== ",data.shape)
    
    # data shape (80, 600, 6), label shape (80,)
    return torch.Tensor(data), torch.Tensor(labels)

# data = np.zeros([80, 144, 299])
# display(csv_data[0:159])
# csv_data.loc[0:159,] = EachColumnMinMax(csv_data[0:159]).copy()
# display(csv_data[0:159])
tmp = {}
display(csv_data[0:144])
for col in csv_data.columns :
    tmp[col] = EachColumnMinMax(csv_data[col][0:159])
#     print(type(EachColumnMinMax(csv_data.loc[0:159, col])))
    display(pd.DataFrame(tmp))
    display(csv_label.values[159 - 1])

# a,b = WindowDataGenerator(csv_data.values, csv_label.values, 24 * 6, 5)
# a.shape

open        high         low       close      volume         value  \
0    60903000.0  61141000.0  60871000.0  60916000.0   63.779659  3.892781e+09   
1    60916000.0  61046000.0  60769000.0  60883000.0   49.432295  3.008935e+09   
2    60879000.0  61300000.0  60878000.0  61106000.0   63.045267  3.852772e+09   
3    61142000.0  61299000.0  61095000.0  61233000.0   42.521032  2.603927e+09   
4    61233000.0  61244000.0  61151000.0  61200000.0   32.518230  1.989991e+09   
5    61200000.0  61220000.0  61140000.0  61145000.0   35.388684  2.165039e+09   
6    61145000.0  61145000.0  61056000.0  61062000.0   43.336748  2.647423e+09   
7    61063000.0  61240000.0  61049000.0  61198000.0   67.962853  4.155542e+09   
8    61196000.0  61249000.0  60900000.0  60938000.0  105.844950  6.467655e+09   
9    60938000.0  61440000.0  60938000.0  61432000.0   97.289920  5.958085e+09   
10   61432000.0  61519000.0  61386000.0  61439000.0  110.870231  6.812963e+09   
11   61442000.0  61443000.0  61243000.0  61370000.0   79.521331  4.881585e+09   
12   61370000.0  61650000.0  61368000.0  61645000.0   78.199001  4.811133e+09   
13   61646000.0  61660000.0  61400000.0  61419000.0   54.312355  3.343400e+09   
14   61400000.0  61430000.0  61033000.0  61070000.0   51.186595  3.137402e+09   
15   61070000.0  61108000.0  60897000.0  60909000.0   63.135771  3.849642e+09   
16   60910000.0  61100000.0  60900000.0  60900000.0   44.588205  2.720505e+09   
17   60900000.0  60900000.0  60800000.0  60835000.0   70.377625  4.281537e+09   
18   60837000.0  60837000.0  60700000.0  60802000.0   57.186062  3.475667e+09   
19   60800000.0  60873000.0  60770000.0  60862000.0   41.376500  2.517044e+09   
20   60860000.0  60976000.0  60846000.0  60918000.0   34.980476  2.131067e+09   
21   60918000.0  61000000.0  60902000.0  60905000.0   31.955973  1.948216e+09   
22   60904000.0  60980000.0  60854000.0  60964000.0   23.980232  1.460506e+09   
23   60980000.0  60998000.0  60962000.0  60988000.0   26.646769  1.625002e+09   
24   60988000.0  61016000.0  60940000.0  60999000.0   24.096548  1.469564e+09   
25   61000000.0  61034000.0  60960000.0  60977000.0   30.854002  1.881733e+09   
26   60977000.0  61000000.0  60950000.0  60973000.0   18.145168  1.106465e+09   
27   60973000.0  60989000.0  60800000.0  60800000.0   30.736614  1.871642e+09   
28   60801000.0  60802000.0  60654000.0  60671000.0   41.955329  2.548625e+09   
29   60671000.0  60671000.0  60505000.0  60600000.0   46.318292  2.807033e+09   
30   60612000.0  60699000.0  60600000.0  60698000.0   22.867369  1.386974e+09   
31   60698000.0  60698000.0  60647000.0  60664000.0   26.636227  1.615973e+09   
32   60664000.0  60868000.0  60661000.0  60726000.0   34.746895  2.110331e+09   
33   60751000.0  60751000.0  60623000.0  60653000.0   34.581096  2.098211e+09   
34   60654000.0  60682000.0  60506000.0  60682000.0   40.882030  2.475836e+09   
35   60682000.0  60682000.0  60550000.0  60613000.0   28.351046  1.717900e+09   
36   60605000.0  60650000.0  60512000.0  60642000.0   28.937719  1.753484e+09   
37   60642000.0  60741000.0  60642000.0  60731000.0   49.142320  2.982950e+09   
38   60726000.0  60768000.0  60520000.0  60521000.0   42.533907  2.580472e+09   
39   60542000.0  60883000.0  60521000.0  60723000.0  116.427886  7.067138e+09   
40   60723000.0  60967000.0  60676000.0  60842000.0  145.436923  8.841984e+09   
41   60807000.0  60842000.0  60754000.0  60757000.0   79.449825  4.829708e+09   
42   60797000.0  60800000.0  60548000.0  60566000.0   80.798858  4.901453e+09   
43   60566000.0  60643000.0  60448000.0  60448000.0   98.329919  5.953844e+09   
44   60447000.0  60641000.0  60410000.0  60499000.0   76.362810  4.618629e+09   
45   60499000.0  60718000.0  60465000.0  60696000.0   94.400546  5.718257e+09   
46   60696000.0  60827000.0  60649000.0  60811000.0  120.907754  7.343459e+09   
47   60816000.0  60817000.0  60658000.0  60767000.0  101.418095  6.161546e+09   
48   60710000.0  60862000.0  60700000.0  6

open
0    0.622267
1    0.628876
2    0.610066
3    0.743772
4    0.790036
5    0.773259
6    0.745297
7    0.703610
8    0.771225
9    0.640061
10   0.891205
11   0.896289
12   0.859685
13   1.000000
14   0.874936
15   0.707168
16   0.625826
17   0.620742
18   0.588714
19   0.569903
20   0.600407
21   0.629893
22   0.622776
23   0.661413
24   0.665480
25   0.671581
26   0.659888
27   0.657855
28   0.570412
29   0.504321
30   0.474326
31   0.518048
32   0.500763
33   0.544992
34   0.495679
35   0.509914
36   0.470768
37   0.489578
38   0.532283
39   0.438739
40   0.530757
41   0.573462
42   0.568378
43   0.450941
44   0.390442
45   0.416878
46   0.517031
47   0.578038
48   0.524148
49   0.597356
50   0.595831
51   0.629893
52   0.592781
53   0.615658
54   0.618200
55   0.576004
56   0.607524
57   0.591256
58   0.592781
59   0.556177
60   0.611083
61   0.639553
62   0.557702
63   0.598882
64   0.651246
65   0.621251
66   0.670564
67   0.636502
68   0.671581
69   0.786985
70   0.856634
71   0.772242
72   0.815963
73   0.820539
74   0.799187
75   0.692933
76   0.673106
77   0.710727
78   0.748348
79   0.824098
80   0.788510
81   0.778851
82   0.716828
83   0.735130
84   0.747839
85   0.578038
86   0.519573
87   0.412303
88   0.408744
89   0.529232
90   0.493137
91   0.563294
92   0.647178
93   0.533299
94   0.491612
95   0.537875
96   0.526690
97   0.477885
98   0.430605
99   0.351296
100  0.352822
101  0.440773
102  0.482461
103  0.467717
104  0.487036
105  0.435180
106  0.367056
107  0.432639
108  0.392984
109  0.494154
110  0.467209
111  0.311642
112  0.362989
113  0.307575
114  0.270463
115  0.288256
116  0.263345
117  0.346213
118  0.309100
119  0.334011
120  0.237417
121  0.229792
122  0.234875
123  0.239451
124  0.180986
125  0.139298
126  0.188104
127  0.146924
128  0.182511
129  0.234875
130  0.261312
131  0.418404
132  0.402135
133  0.260803
134  0.213523
135  0.315201
136  0.256736
137  0.277072
138  0.276055
139  0.272496
140  0.282664
141  0.081342
142  0.125572
143  0.093543
144  0.185053
145  0.162176
146  0.159126
147  0.067107
148  0.073208
149  0.065582
150  0.037112
151  0.000000
152  0.071683
153  0.159126
154  0.145907
155  0.051856
156  0.059990
157  0.123030
158  0.124555

array([1.])

open      high
0    0.622267  0.727987
1    0.628876  0.678197
2    0.610066  0.811321
3    0.743772  0.810797
4    0.790036  0.781971
5    0.773259  0.769392
6    0.745297  0.730084
7    0.703610  0.779874
8    0.771225  0.784591
9    0.640061  0.884696
10   0.891205  0.926101
11   0.896289  0.886268
12   0.859685  0.994759
13   1.000000  1.000000
14   0.874936  0.879455
15   0.707168  0.710692
16   0.625826  0.706499
17   0.620742  0.601677
18   0.588714  0.568658
19   0.569903  0.587526
20   0.600407  0.641509
21   0.629893  0.654088
22   0.622776  0.643606
23   0.661413  0.653040
24   0.665480  0.662474
25   0.671581  0.671908
26   0.659888  0.654088
27   0.657855  0.648323
28   0.570412  0.550314
29   0.504321  0.481656
30   0.474326  0.496331
31   0.518048  0.495807
32   0.500763  0.584906
33   0.544992  0.523585
34   0.495679  0.487421
35   0.509914  0.487421
36   0.470768  0.470650
37   0.489578  0.518344
38   0.532283  0.532495
39   0.438739  0.592767
40   0.530757  0.636792
41   0.573462  0.571279
42   0.568378  0.549266
43   0.450941  0.466981
44   0.390442  0.465933
45   0.416878  0.506289
46   0.517031  0.563417
47   0.578038  0.558176
48   0.524148  0.581761
49   0.597356  0.629979
50   0.595831  0.632600
51   0.629893  0.612683
52   0.592781  0.612683
53   0.615658  0.612159
54   0.618200  0.612159
55   0.576004  0.627883
56   0.607524  0.611111
57   0.591256  0.606918
58   0.592781  0.680294
59   0.556177  0.601677
60   0.611083  0.654088
61   0.639553  0.643082
62   0.557702  0.583857
63   0.598882  0.640985
64   0.651246  0.651992
65   0.621251  0.654088
66   0.670564  0.654088
67   0.636502  0.671908
68   0.671581  0.794025
69   0.786985  0.862159
70   0.856634  0.846436
71   0.772242  0.812893
72   0.815963  0.813941
73   0.820539  0.810273
74   0.799187  0.813941
75   0.692933  0.721698
76   0.673106  0.694969
77   0.710727  0.766247
78   0.748348  0.916143
79   0.824098  0.830713
80   0.788510  0.781447
81   0.778851  0.765199
82   0.716828  0.755765
83   0.735130  0.752096
84   0.747839  0.733229
85   0.578038  0.589099
86   0.519573  0.538784
87   0.412303  0.444444
88   0.408744  0.551363
89   0.529232  0.550314
90   0.493137  0.549266
91   0.563294  0.765723
92   0.647178  0.631027
93   0.533299  0.511530
94   0.491612  0.540881
95   0.537875  0.589099
96   0.526690  0.504717
97   0.477885  0.464885
98   0.430605  0.415094
99   0.351296  0.392034
100  0.352822  0.417715
101  0.440773  0.505241
102  0.482461  0.496855
103  0.467717  0.476939
104  0.487036  0.475367
105  0.435180  0.474319
106  0.367056  0.457023
107  0.432639  0.453354
108  0.392984  0.549266
109  0.494154  0.506289
110  0.467209  0.470126
111  0.311642  0.362159
112  0.362989  0.368973
113  0.307575  0.325996
114  0.270463  0.302411
115  0.288256  0.305556
116  0.263345  0.318658
117  0.346213  0.393082
118  0.309100  0.339099
119  0.334011  0.306080
120  0.237417  0.253145
121  0.229792  0.224319
122  0.234875  0.228512
123  0.239451  0.208595
124  0.180986  0.148323
125  0.139298  0.156709
126  0.188104  0.156184
127  0.146924  0.177149
128  0.182511  0.231132
129  0.234875  0.234277
130  0.261312  0.424004
131  0.418404  0.420860
132  0.402135  0.376834
133  0.260803  0.288260
134  0.213523  0.287212
135  0.315201  0.286688
136  0.256736  0.277254
137  0.277072  0.248428
138  0.276055  0.246331
139  0.272496  0.273061
140  0.282664  0.286164
141  0.081342  0.126834
142  0.125572  0.096960
143  0.093543  0.152516
144  0.185053  0.156184
145  0.162176  0.137841
146  0.159126  0.125786
147  0.067107  0.045073
148  0.073208  0.037736
149  0.065582  0.029350
150  0.037112  0.000000
151  0.000000  0.044025
152  0.071683  0.140461
153  0.159126  0.166143
154  0.145907  0.121069
155  0.051856  0.053459
156  0.059990  0.153040
157  0.123030  0.112683
158  0.124555  0.166667

array([1.])

...

array([1.])

open      high       low     close    volume     value
0    0.622267  0.727987  0.721579  0.629196  0.310212  0.317531
1    0.628876  0.678197  0.667895  0.612411  0.222861  0.227549
2    0.610066  0.811321  0.725263  0.725839  0.305741  0.313458
3    0.743772  0.810797  0.839474  0.790437  0.180782  0.186315
4    0.790036  0.781971  0.868947  0.773652  0.119882  0.123811
5    0.773259  0.769392  0.863158  0.745677  0.137358  0.141633
6    0.745297  0.730084  0.818947  0.703459  0.185749  0.190744
7    0.703610  0.779874  0.815263  0.772635  0.335681  0.344283
8    0.771225  0.784591  0.736842  0.640387  0.566321  0.579675
9    0.640061  0.884696  0.756842  0.891658  0.514235  0.527797
10   0.891205  0.926101  0.992632  0.895219  0.596917  0.614830
11   0.896289  0.886268  0.917368  0.860122  0.406053  0.418200
12   0.859685  0.994759  0.983158  1.000000  0.398003  0.411027
13   1.000000  1.000000  1.000000  0.885046  0.252572  0.261600
14   0.874936  0.879455  0.806842  0.707528  0.233541  0.240627
15   0.707168  0.710692  0.735263  0.625636  0.306292  0.313140
16   0.625826  0.706499  0.736842  0.621058  0.193368  0.198184
17   0.620742  0.601677  0.684211  0.587996  0.350383  0.357110
18   0.588714  0.568658  0.631579  0.571211  0.270068  0.275066
19   0.569903  0.587526  0.668421  0.601729  0.173814  0.177470
20   0.600407  0.641509  0.708421  0.630214  0.134873  0.138174
21   0.629893  0.654088  0.737895  0.623601  0.116458  0.119558
22   0.622776  0.643606  0.712632  0.653611  0.067899  0.069905
23   0.661413  0.653040  0.769474  0.665819  0.084134  0.086653
24   0.665480  0.662474  0.757895  0.671414  0.068607  0.070828
25   0.671581  0.671908  0.768421  0.660224  0.109749  0.112790
26   0.659888  0.654088  0.763158  0.658189  0.032373  0.033861
27   0.657855  0.648323  0.684211  0.570193  0.109035  0.111762
28   0.570412  0.550314  0.607368  0.504578  0.177338  0.180685
29   0.504321  0.481656  0.528947  0.468464  0.203901  0.206993
30   0.474326  0.496331  0.578947  0.518311  0.061124  0.062419
31   0.518048  0.495807  0.603684  0.501017  0.084070  0.085733
32   0.500763  0.584906  0.611053  0.532553  0.133451  0.136063
33   0.544992  0.523585  0.591053  0.495422  0.132441  0.134829
34   0.495679  0.487421  0.529474  0.510173  0.170803  0.173274
35   0.509914  0.487421  0.552632  0.475076  0.094510  0.096110
36   0.470768  0.470650  0.532632  0.489827  0.098082  0.099733
37   0.489578  0.518344  0.601053  0.535097  0.221095  0.224903
38   0.532283  0.532495  0.536842  0.428281  0.180861  0.183927
39   0.438739  0.592767  0.537368  0.531027  0.630754  0.640708
40   0.530757  0.636792  0.618947  0.591556  0.807371  0.821402
41   0.573462  0.571279  0.660000  0.548321  0.405618  0.412918
42   0.568378  0.549266  0.551579  0.451170  0.413831  0.420223
43   0.450941  0.466981  0.498947  0.391150  0.520567  0.527365
44   0.390442  0.465933  0.478947  0.417091  0.386823  0.391429
45   0.416878  0.506289  0.507895  0.517294  0.496643  0.503380
46   0.517031  0.563417  0.604737  0.575788  0.658029  0.668839
47   0.578038  0.558176  0.609474  0.553408  0.539369  0.548511
48   0.524148  0.581761  0.631579  0.597660  0.351055  0.357242
49   0.597356  0.629979  0.677368  0.594608  0.642206  0.654481
50   0.595831  0.632600  0.685263  0.627670  0.438834  0.447661
51   0.629893  0.612683  0.672632  0.593082  0.173804  0.177543
52   0.592781  0.612683  0.687895  0.615972  0.143356  0.146579
53   0.615658  0.612159  0.678947  0.608850  0.217359  0.221847
54   0.618200  0.612159  0.688947  0.576297  0.242066  0.247173
55   0.576004  0.627883  0.631053  0.607833  0.332893  0.339198
56   0.607524  0.611111  0.684211  0.585453  0.357914  0.364851
57   0.591256  0.606918  0.700000  0.591556  0.532453  0.542558
58   0.592781  0.680294  0.632105  0.526958  0.725409  0.739465
59   0.556177  0.601677  0.633158  0.610885  0.344329  0.351118
60   0.611083  0.654088  0.726316  0.639878  0.364966  0.372664
61   0.639553  0.643082  0.649474  0.5584

array([1.])

open      high       low     close    volume     value  avg_price
0    0.622267  0.727987  0.721579  0.629196  0.310212  0.317531   0.689370
1    0.628876  0.678197  0.667895  0.612411  0.222861  0.227549   0.659986
2    0.610066  0.811321  0.725263  0.725839  0.305741  0.313458   0.734326
3    0.743772  0.810797  0.839474  0.790437  0.180782  0.186315   0.816385
4    0.790036  0.781971  0.868947  0.773652  0.119882  0.123811   0.824374
5    0.773259  0.769392  0.863158  0.745677  0.137358  0.141633   0.807718
6    0.745297  0.730084  0.818947  0.703459  0.185749  0.190744   0.767502
7    0.703610  0.779874  0.815263  0.772635  0.335681  0.344283   0.786730
8    0.771225  0.784591  0.736842  0.640387  0.566321  0.579675   0.750575
9    0.640061  0.884696  0.756842  0.891658  0.514235  0.527797   0.813541
10   0.891205  0.926101  0.992632  0.895219  0.596917  0.614830   0.952742
11   0.896289  0.886268  0.917368  0.860122  0.406053  0.418200   0.915098
12   0.859685  0.994759  0.983158  1.000000  0.398003  0.411027   0.987542
13   1.000000  1.000000  1.000000  0.885046  0.252572  0.261600   1.000000
14   0.874936  0.879455  0.806842  0.707528  0.233541  0.240627   0.838592
15   0.707168  0.710692  0.735263  0.625636  0.306292  0.313140   0.710088
16   0.625826  0.706499  0.736842  0.621058  0.193368  0.198184   0.686527
17   0.620742  0.601677  0.684211  0.587996  0.350383  0.357110   0.635748
18   0.588714  0.568658  0.631579  0.571211  0.270068  0.275066   0.600677
19   0.569903  0.587526  0.668421  0.601729  0.173814  0.177470   0.618145
20   0.600407  0.641509  0.708421  0.630214  0.134873  0.138174   0.658091
21   0.629893  0.654088  0.737895  0.623601  0.116458  0.119558   0.675017
22   0.622776  0.643606  0.712632  0.653611  0.067899  0.069905   0.671903
23   0.661413  0.653040  0.769474  0.665819  0.084134  0.086653   0.702505
24   0.665480  0.662474  0.757895  0.671414  0.068607  0.070828   0.704536
25   0.671581  0.671908  0.768421  0.660224  0.109749  0.112790   0.708328
26   0.659888  0.654088  0.763158  0.658189  0.032373  0.033861   0.698714
27   0.657855  0.648323  0.684211  0.570193  0.109035  0.111762   0.652945
28   0.570412  0.550314  0.607368  0.504578  0.177338  0.180685   0.567095
29   0.504321  0.481656  0.528947  0.468464  0.203901  0.206993   0.501963
30   0.474326  0.496331  0.578947  0.518311  0.061124  0.062419   0.523900
31   0.518048  0.495807  0.603684  0.501017  0.084070  0.085733   0.537170
32   0.500763  0.584906  0.611053  0.532553  0.133451  0.136063   0.565877
33   0.544992  0.523585  0.591053  0.495422  0.132441  0.134829   0.546784
34   0.495679  0.487421  0.529474  0.510173  0.170803  0.173274   0.512390
35   0.509914  0.487421  0.552632  0.475076  0.094510  0.096110   0.512796
36   0.470768  0.470650  0.532632  0.489827  0.098082  0.099733   0.496818
37   0.489578  0.518344  0.601053  0.535097  0.221095  0.224903   0.543805
38   0.532283  0.532495  0.536842  0.428281  0.180861  0.183927   0.513879
39   0.438739  0.592767  0.537368  0.531027  0.630754  0.640708   0.532024
40   0.530757  0.636792  0.618947  0.591556  0.807371  0.821402   0.605010
41   0.573462  0.571279  0.660000  0.548321  0.405618  0.412918   0.598510
42   0.568378  0.549266  0.551579  0.451170  0.413831  0.420223   0.537712
43   0.450941  0.466981  0.498947  0.391150  0.520567  0.527365   0.455653
44   0.390442  0.465933  0.478947  0.417091  0.386823  0.391429   0.441029
45   0.416878  0.506289  0.507895  0.517294  0.496643  0.503380   0.492620
46   0.517031  0.563417  0.604737  0.575788  0.658029  0.668839   0.574543
47   0.578038  0.558176  0.609474  0.553408  0.539369  0.548511   0.584699
48   0.524148  0.581761  0.631579  0.597660  0.351055  0.357242   0.593907
49   0.597356  0.629979  0.677368  0.594608  0.642206  0.654481   0.636831
50   0.595831  0.632600  0.685263  0.627670  0.438834  0.447661   0.647935
51   0.629893  0.612683  0.672632  0.593082  0.173804  0.177543   0.639404
52   0.592781  0.612683  0.687895 

array([1.])

In [11]:
pd.set_option('display.max_rows', None)
csv_label.iloc[167:190]

after10
167      1.0
168      0.0
169      1.0
170      0.0
171      0.0
172      0.0
173      0.0
174      1.0
175      1.0
176      1.0
177      0.0
178      0.0
179      0.0
180      1.0
181      1.0
182      0.0
183      0.0
184      1.0
185      1.0
186      0.0
187      0.0
188      0.0
189      1.0

In [43]:
# def EachColumnMinMax(df_data) :
#     norm = MinMaxScaler()
#     for col in df_data.columns :
#         df_2d = np.array(df_data[col]).reshape(-1, 1)
#         print(df_2d.shape)
# #         norm_dataset = norm.fit_transform(df_data[col])
#         df_data.loc[:, col] = norm.fit_transform(df_2d).squeeze(1)
        
#     return df_data

def EachColumnMinMax(df_data) :
    norm = MinMaxScaler()
    df_data = norm.fit_transform(np.array(df_data).reshape(-1, 1)).squeeze(1)
    return df_data

def WindowDataGenerator(df_data, df_label, window_size, stride) :
    num_sample = (df_data.shape[0] - window_size) // stride + 1     

    data = np.zeros([window_size, df_data.shape[1], num_sample])
    labels = np.zeros([num_sample])

    for i in tqdm(range(num_sample)) :
        tmp = {}
        data_start = stride * i
        data_end = data_start + window_size
        for col in df_data.columns :
            tmp[col] = EachColumnMinMax(df_data[col][data_start : data_end])
#         display(pd.DataFrame(tmp))
#         display(df_data[data_start : data_end])
        data[:, :, i] = pd.DataFrame(tmp).values
        labels[i] = df_label.values[data_end - 1]
        
    data = data.transpose((2, 0, 1))
    print("dataset shape ==== ",data.shape)
    
    # data shape (80, 600, 6), label shape (80,)
    return torch.Tensor(data), torch.Tensor(labels)

display(csv_data.shape)

a,b = WindowDataGenerator(csv_data, csv_label, 24 * 6, 5)
a.shape

(9999, 7)

100%|█████████████████████████████████████████████████████████████████████████████| 1972/1972 [00:04<00:00, 483.90it/s]

dataset shape ====  (1972, 144, 7)


torch.Size([1972, 144, 7])

In [44]:
for o in b :
    print(o)

tensor(0.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(0.)

tensor(1.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(1.)
tensor(0.)
tensor(1.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(0.)
tensor(1.)
tensor(0.)

# Window Dataset

In [45]:
class WindowDataset(Dataset) :
    def __init__(self, df_data, df_label, window_size=144, stride=6) :
        self.data, self.label = self.WindowDataGenerator(df_data, df_label, window_size, stride)        
        
    def __getitem__(self, i) :
        return self.data[i], self.label[i]
                
    def __len__(self) :
        assert len(self.data) == len(self.label), "data와 label의 길이가 다름"
        return len(self.data)
        
    
    def WindowDataGenerator(self, df_data, df_label, window_size, stride) :
        num_sample = (df_data.shape[0] - window_size) // stride + 1     

        data = np.zeros([window_size, df_data.shape[1], num_sample])
        labels = np.zeros([num_sample])

        for i in tqdm(range(num_sample)) :
            tmp = {}
            data_start = stride * i
            data_end = data_start + window_size
            for col in df_data.columns :
                tmp[col] = EachColumnMinMax(df_data[col][data_start : data_end])

            data[:, :, i] = pd.DataFrame(tmp).values
            labels[i] = df_label.values[data_end - 1]

        data = data.transpose((2, 0, 1))
        # data shape (80, 600, 6), label shape (80,)
        return torch.Tensor(data), torch.Tensor(labels)
    
    def EachColumnMinMax(self, df_data) :
        norm = MinMaxScaler()
        df_data = norm.fit_transform(np.array(df_data).reshape(-1, 1)).squeeze(1)
        return df_data

    def WindowDataGenerator(self, df_data, df_label, window_size, stride) :
        num_sample = (df_data.shape[0] - window_size) // stride + 1     

        data = np.zeros([window_size, df_data.shape[1], num_sample])
        labels = np.zeros([num_sample])

        for i in tqdm(range(num_sample)) :
            tmp = {}
            data_start = stride * i
            data_end = data_start + window_size
            for col in df_data.columns :
                tmp[col] = self.EachColumnMinMax(df_data.loc[data_start : data_end - 1, col])

            data[:, :, i] = pd.DataFrame(tmp).values
            labels[i] = df_label.values[data_end - 1]

        data = data.transpose((2, 0, 1))
        print("dataset shape ==== ",data.shape)

        # data shape (80, 600, 6), label shape (80,)
        return torch.Tensor(data), torch.Tensor(labels)

# nn.Transformer

In [46]:
class Transformer2FC(nn.Module) :
    def __init__(self, input_shape, d_model, n_head, num_layer, dropout, num_class=2):
        super(Transformer2FC, self).__init__()
        
        self.encoder_layer = nn.TransformerEncoderLayer(d_model=d_model, nhead=n_head, dropout=dropout)
        self.transformer_encoder = nn.TransformerEncoder(self.encoder_layer, num_layers=num_layer)
        self.pos_encoder = PositionalEncoding(d_model, dropout)
        
        self.Encoder = nn.Sequential(
            nn.Linear(input_shape[1], d_model//2),
            nn.ReLU(),
            nn.Linear(d_model//2, d_model)
        )
        
        self.linear = nn.Sequential(
            nn.Linear(d_model, d_model//2),
            nn.ReLU(),
            nn.Linear(d_model//2, 1)
        )

        self.linear2 = nn.Sequential(
            nn.Linear(input_shape[0], input_shape[0]//2),
            nn.ReLU(),
            nn.Linear(input_shape[0]//2, num_class)
        )
        
#         self.sigmoid = nn.Softmax()
    
    def generate_square_subsequent_mask(self, sz):
        mask = (torch.triu(torch.ones(sz, sz)) == 1).transpose(0, 1)
        mask = mask.float().masked_fill(mask == 0, float('-inf')).masked_fill(mask == 1, float(0.0))
        return mask
    
    def forward(self, x, masked_x) :
        # (batch, data, dim)
#         print("input shape : ", x.shape)
        x = self.Encoder(x)
#         print("Encoder shape : ", x.shape)
        x = self.pos_encoder(x)
#         print("pos_encoder shape : ", x.shape)
#         print("masked_x shape : ", masked_x.shape)
        x = self.transformer_encoder(x.transpose(0,1), masked_x).transpose(0, 1)
#         print("transformer_encoder shape : ", x.shape)
        x = self.linear(x)
#         print("linear shape : ", x.shape)
        x = x.squeeze(2)
#         print("squeeze shape : ", x.shape)
        x = self.linear2(x)
#         print("linear2 shape : ", x.shape)
        x = x.squeeze(1)
#         print("squeeze shape : ", x.shape)
        return x

class PositionalEncoding(nn.Module) :
    def __init__(self, d_model, dropout=0.1, max_len=5000) :
        super(PositionalEncoding, self).__init__()
        self.dropout = nn.Dropout(p=dropout)
        
        pe = torch.zeros(max_len, d_model)
        
        position = torch.arange(0, max_len, dtype=torch.float).unsqueeze(1)
        div_term = torch.exp(torch.arange(0, d_model, 2).float() * (-math.log(10000.0) / d_model))
        pe[:, 0::2] = torch.sin(position * div_term)
        pe[:, 1::2] = torch.cos(position * div_term)
        pe = pe.unsqueeze(0).transpose(0, 1)
        self.register_buffer('pe', pe)
        
    def forward(self, x) :
        x = x + self.pe[:x.size(0), :]

        return self.dropout(x)

def get_attention_mask(x) :
    mask = torch.eq(x, 0)
    return mask

In [47]:
device = torch.device("cuda")
lr = 1e-4
epoch = 500
window_size = 24 * 6
window_stride = 6
feature_len = 7
batch_size = 64
num_class = 1

model = Transformer2FC(input_shape=(window_size, feature_len), 
                       d_model=512, 
                       n_head=8, 
                       num_layer=4, 
                       dropout=0.3, 
                       num_class = num_class).to(device)
# model = MLSTMfcn(max_seq_len=window_size, num_features=feature_len).to(device)
criterion = nn.BCEWithLogitsLoss()
# criterion = nn.CrossEntropyLoss()
# criterion = nn.HuberLoss()
optim = torch.optim.Adam(model.parameters(), lr=lr)

In [48]:
dataset = WindowDataset(csv_data, 
                        csv_label,
                       window_size = window_size, 
                       stride = window_stride)
# dataset = WindowDataset(csv_data.values, 
#                         csv_label.values, 
#                        window_size = window_size, 
#                        stride = window_stride)
dataloader = DataLoader(dataset, batch_size=batch_size)

100%|█████████████████████████████████████████████████████████████████████████████| 1643/1643 [00:03<00:00, 451.13it/s]

dataset shape ====  (1643, 144, 7)


In [49]:
def cal_accuracy(pred, label, threshold=0) :
    acc = torch.zeros(pred.shape[0])
    acc[pred > threshold] = 1
    acc[pred < threshold] = 0
    score = [1 if acc[i] == label[i] else 0 for i in range(pred.shape[0])]
    return sum(score) / pred.shape[0]

In [50]:
# def cal_accuracy(pred, label, threshold=0.5) :
#     res = torch.argmax(pred, dim=1)
    
#     print(pred)
#     print(res)
#     print(label)

#     score = [1 if res[i] == label[i] else 0 for i in range(pred.shape[0])]
#     return sum(score) / pred.shape[0]

In [51]:
progress = tqdm(range(epoch))

model.train()
for i in progress :
    batchloss = 0.0
    batchacc= 0
    for (data, label) in dataloader :
        optim.zero_grad()
        src_mask = model.generate_square_subsequent_mask(data.shape[1]).to(device)      
        
        pred = model(data.to(device), src_mask)
        
        loss = criterion(pred, label.to(device, dtype=torch.float64))
#         print(data.shape)
#         print(pred.shape)
        loss.backward()
        optim.step()
        
        score = cal_accuracy(pred.cpu(), label.cpu())
        progress.set_description("loss : {:0.6f} acc : {:0.6f}".format(loss.cpu().item(), score))
#         progress.set_description("loss : {:0.6f}".format(loss.cpu().item()))
        
        batchloss += loss
        batchacc += score
    print(f"Epoch : [{i} / {epoch}] Loss : {round((batchloss/len(dataloader)).item(), 4)} Acc : {round((batchacc/len(dataloader)), 4)}")
#     print(pred)
#     print(label)
#     print(f"Epoch : [{i} / {epoch}] Loss : {round((batchloss/len(dataloader)).item(), 4)}")
    
torch.save(model.state_dict(), f'./model.pt')

loss : 0.693245 acc : 0.531250:   0%|                                                  | 1/500 [00:04<36:27,  4.38s/it]

Epoch : [0 / 500] Loss : 0.6934 Acc : 0.5074


loss : 0.691190 acc : 0.578125:   0%|▏                                                 | 2/500 [00:08<36:10,  4.36s/it]

Epoch : [1 / 500] Loss : 0.6934 Acc : 0.5011


loss : 0.696061 acc : 0.406250:   1%|▎                                                 | 3/500 [00:13<36:09,  4.37s/it]

...

Epoch : [497 / 500] Loss : 0.6934 Acc : 0.5004


loss : 0.691748 acc : 0.593750: 100%|███████████████████████████████████████████████▉| 499/500 [40:00<00:04,  4.86s/it]

Epoch : [498 / 500] Loss : 0.6934 Acc : 0.5131


loss : 0.693806 acc : 0.465116: 100%|████████████████████████████████████████████████| 500/500 [40:05<00:00,  4.81s/it]


Epoch : [499 / 500] Loss : 0.6933 Acc : 0.4981


In [ ]:
torch.save(model.state_dict(), f'./model.pt')

In [ ]:
__output = torch.full([10, 64], 1.5)
__output.type()

In [20]:
data = torch.rand(2, 144, 6).to(device)
data
src_mask = model.generate_square_subsequent_mask(data.shape[1]).to(device)  
re = model(data, src_mask)
re

tensor([-0.0590, -0.0577], device='cuda:0', grad_fn=<SqueezeBackward1>)

# MLSTM-fcn

In [ ]:
class SELayer(nn.Module):
    def __init__(self, channel, reduction=16):
        super(SELayer, self).__init__()
        self.avg_pool = nn.AdaptiveAvgPool1d(1)
        self.fc = nn.Sequential(
            nn.Linear(channel, channel // reduction, bias=False),
            nn.ReLU(inplace=True),
            nn.Linear(channel // reduction, channel, bias=False),
            nn.Sigmoid()
        )

    def forward(self, x):
        b, c, _ = x.size()
        y = self.avg_pool(x).view(b, c)
        y = self.fc(y).view(b, c, 1)
        return x * y.expand_as(x)

class MLSTMfcn(nn.Module):
    def __init__(self, *, num_classes=1, max_seq_len=144, num_features=6,
                 num_lstm_out=128, num_lstm_layers=1, 
                 conv1_nf=128, conv2_nf=256, conv3_nf=128,
                 lstm_drop_p=0.8, fc_drop_p=0.3):
        
        super(MLSTMfcn, self).__init__()
        self.num_classes = num_classes
        self.max_seq_len = max_seq_len
        self.num_features = num_features

        self.num_lstm_out = num_lstm_out
        self.num_lstm_layers = num_lstm_layers

        self.conv1_nf = conv1_nf
        self.conv2_nf = conv2_nf
        self.conv3_nf = conv3_nf

        self.lstm_drop_p = lstm_drop_p
        self.fc_drop_p = fc_drop_p

        self.lstm = nn.LSTM(input_size=self.num_features, 
                            hidden_size=self.num_lstm_out,
                            num_layers=self.num_lstm_layers,
                            batch_first=True)
        
        self.conv1 = nn.Conv1d(self.num_features, self.conv1_nf, 8)
        self.conv2 = nn.Conv1d(self.conv1_nf, self.conv2_nf, 5)
        self.conv3 = nn.Conv1d(self.conv2_nf, self.conv3_nf, 3)

        self.bn1 = nn.BatchNorm1d(self.conv1_nf)
        self.bn2 = nn.BatchNorm1d(self.conv2_nf)
        self.bn3 = nn.BatchNorm1d(self.conv3_nf)

        self.se1 = SELayer(self.conv1_nf)  # ex 128
        self.se2 = SELayer(self.conv2_nf)  # ex 256

        self.relu = nn.ReLU()
        self.lstmDrop = nn.Dropout(self.lstm_drop_p)
        self.convDrop = nn.Dropout(self.fc_drop_p)

        self.fc = nn.Sequential(
            nn.Linear(self.conv3_nf+self.num_lstm_out, 128),
            nn.ReLU(),
            nn.Linear(128, self.num_classes)
        )

#         self.out_layer = nn.Linear(1000+128, self.num_classes)
#         self.dropout = nn.Dropout(0.1)
    
    def forward(self, x):
        ''' input x should be in size [B,T,F], where 
            B = Batch size
            T = Time samples
            F = features
        '''
#         x1 = nn.utils.rnn.pack_padded_sequence(x, seq_lens.cpu(), 
#                                                batch_first=True, 
#                                                enforce_sorted=False)
#         x1 = nn.utils.rnn.pack_padded_sequence(x, seq_lens, 
#                                                batch_first=True, 
#                                                enforce_sorted=False)
        
        x1, (ht,ct) = self.lstm(x)
#         x1, _ = nn.utils.rnn.pad_packed_sequence(x1, batch_first=True, 
#                                                  padding_value=0.0)
        x1 = x1[:,-1,:]
        
        x2 = x.transpose(2,1)
        x2 = self.convDrop(self.relu(self.bn1(self.conv1(x2))))
        x2 = self.se1(x2)
        x2 = self.convDrop(self.relu(self.bn2(self.conv2(x2))))
        x2 = self.se2(x2)
        x2 = self.convDrop(self.relu(self.bn3(self.conv3(x2))))
        x2 = torch.mean(x2,2)
        
        x_all = torch.cat((x1,x2),dim=1)
        x_out = self.fc(x_all)
#         concat = torch.cat([enc_out, x_out], dim=1)  # enc_out + hidden 
#         output = self.dropout(concat)
#         x_output = self.out_layer(output)
#         x_out = F.log_softmax(x_out, dim=1)

        return x_out

In [19]:
class Data_preprocess() :
    def __init__(self, ticker=None, interval=None, to=None, count=None, df=None, csv_list=None) :
        if ticker and interval and to and count :
            self.data, self.label, self.dataset = self.preprocess(pyupbit.get_ohlcv(ticker=ticker, interval=interval, to=to, count=count))
        elif  df :
            self.data, self.label, self.dataset = self.preprocess(df)
            
        elif csv_list :
            for csv_path in csv_list :
                try :
                    df = pd.read_csv(csv_path)
                    csv_data, csv_label, _ = self.preprocess(df)

                    fold_name = csv_path.split('\\')[-2]
                    file_name = csv_path.split('\\')[-1]
                    new_path = csv_path.replace(fold_name, 'preprocess_'+fold_name).replace(csv_path.split('\\')[-1],'')
                    os.makedirs(new_path, exist_ok=True)
                    
                    csv_dataset = pd.concat([csv_data, csv_label], axis=1)
                    csv_dataset.to_csv(os.path.join(new_path, file_name))
                    
                except :
                    print(f"ERROR from {csv_path}")
            
            
            
    def MinMax(self, dataset_df) :
        norm = MinMaxScaler()
        norm_dataset = norm.fit_transform(dataset_df)
        return pd.DataFrame(norm_dataset, columns=list(dataset_df.columns))
    
    
    def add_after10(self, dataset_df) :
        after10 = np.zeros_like(self.norm_dataset['close'])
        for i in range(len(dataset_df['close']) - 1) :
            if dataset_df['close'][i + 1] > dataset_df['close'][i] :
                after10[i] = 1
            else : 
                after10[i] = 0
            
        return after10
    
    
    def drop_feature(self, dataset_df) :
        # index(시간) 제거 
        dataset_df = dataset_df.drop(columns=['Unnamed: 0'])
        # value 제거
        dataset_df = dataset_df.drop(columns=['value'])
        return dataset_df
    
    
    def add_avgPrice(self, dataset_df) :
        return (dataset_df['high'] + dataset_df['low'] + 
                dataset_df['open'] + dataset_df['close']) // 4
       
    
    def preprocess(self, dataset, latest=False) :
        
        # drop feature
        dataset_df = self.drop_feature(dataset)
#         display(dataset_df)
        # avg_price 추가
        dataset_df['avg_price'] = self.add_avgPrice(dataset_df)
        
        if latest == True :
            # 가장 예전 데이터 삭제 - norm이랑 original 둘 다 적용
            self.dataset = self.dataset.drop([self.dataset.index[0]]).drop(columns=['after10'])
            self.norm_dataset = self.norm_dataset.drop([self.norm_dataset.index[0]])

            # ori dataset에 추가
            self.dataset = pd.concat([self.dataset, dataset_df])
            self.dataset = self.dataset.reset_index(drop=True)
            
            # min max 정규화 (MinMaxScaler) 적용
            self.norm_dataset = self.MinMax(self.dataset)
            
            # after10 추가
            self.dataset['after10'] = self.add_after10(self.dataset)
            
        
        else :
            # min max 정규화 (MinMaxScaler) 적용
            self.norm_dataset = self.MinMax(dataset_df)
            
            # after10 추가
            dataset_df['after10'] = self.add_after10(dataset_df)
        
        # 예측될 값(label)인 10분 후 가격
        self.norm_dataset['after10'] = self.add_after10(self.norm_dataset)
        
        # 마지막 행 삭제 (다음 가격을 모르므로 라벨을 붙일 수 없음)
        self.norm_dataset = self.norm_dataset.iloc[:-1]
        
        return self.norm_dataset.drop(columns=['after10']), self.norm_dataset['after10'], dataset_df
    
